<a href="https://colab.research.google.com/github/softmurata/colab_notebooks/blob/main/animation/RAD_NeRF.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# [RAD-NeRF](https://github.com/ashawkey/RAD-NeRF) for Real-time Neural Talking Portrait Synthesis

### Check the machine

In [ ]:
! nvidia-smi

Wed Nov 23 04:33:05 2022       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.32.03    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   49C    P8     9W /  70W |      0MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [ ]:
#@title install dependencies
! git clone https://github.com/ashawkey/RAD-NeRF.git

%cd RAD-NeRF

%mkdir -p pretrained
%mkdir -p data

Cloning into 'RAD-NeRF'...
remote: Enumerating objects: 95, done.
remote: Counting objects: 100% (95/95), done.
remote: Compressing objects: 100% (78/78), done.
remote: Total 95 (delta 16), reused 91 (delta 12), pack-reused 0
Unpacking objects: 100% (95/95), done.
/content/RAD-NeRF


In [ ]:
# install (slow...)
! apt install libasound2-dev portaudio19-dev libportaudio2 libportaudiocpp0 ffmpeg
! pip install -r requirements.txt
! pip install ffmpeg-python
! bash scripts/install_ext.sh

Reading package lists... Done
Building dependency tree       
Reading state information... Done
libasound2-dev is already the newest version (1.1.3-5ubuntu0.6).
ffmpeg is already the newest version (7:3.4.11-0ubuntu0.1).
The following package was automatically installed and is no longer required:
  libnvidia-common-460
Use 'apt autoremove' to remove it.
Suggested packages:
  portaudio19-doc
The following NEW packages will be installed:
  libportaudio2 libportaudiocpp0 portaudio19-dev
0 upgraded, 3 newly installed, 0 to remove and 5 not upgraded.
Need to get 184 kB of archives.
After this operation, 891 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic/universe amd64 libportaudio2 amd64 19.6.0-1 [64.6 kB]
Get:2 http://archive.ubuntu.com/ubuntu bionic/universe amd64 libportaudiocpp0 amd64 19.6.0-1 [15.1 kB]
Get:3 http://archive.ubuntu.com/ubuntu bionic/universe amd64 portaudio19-dev amd64 19.6.0-1 [104 kB]
Fetched 184 kB in 1s (317 kB/s)
Selecting pr

# Settings
* Person: choose a pretrained person-specific model.
* Audio: choose a provided audio file, or upload your own (choose `custom`).
* Background: choose a provided background image, or upload your own (choose `custom`).
* Pose_start/end: data range to use from pose.json.

In [ ]:
#@markdown ####**Settings:**
Person = 'engm' #@param ['obama', 'marco', 'engm', 'chris']
Audio = 'intro' #@param ['intro', 'nvp', 'custom']
Background = 'default' #@param ['default', 'custom']
Pose_start = 0 #@param {type: 'integer'}
Pose_end = 100 #@param {type: 'integer'}

In [ ]:
#@title Upload audio if choose custom (*.wav format)
if Audio == 'custom':
    %cd data/
    from google.colab import files
    uploaded = files.upload()
    Aud = os.path.basename(next(iter(uploaded))) # filename, should be '*.wav'
    assert Aud[-4:] == '.wav', f'[ERROR] must upload *.wav audio file'
    %cd ..
else:
    Aud = Audio + '.wav'

print(f'[INFO] use audio file: {Aud}')

[INFO] use audio file: intro.wav


In [ ]:
#@title Upload background image if choose custom
if Background == 'custom':
    %cd data/
    from google.colab import files
    uploaded = files.upload()
    BG = os.path.basename(next(iter(uploaded))) # filename, should be '*.wav'
    %cd ..
else:
    BG = 'bg.jpg'

print(f'[INFO] use background file: {BG}')

[INFO] use background file: bg.jpg


In [ ]:
#@title Download things

import gdown

# model checkpoint and pose sequence
if Person == 'obama':
    gdown.download("https://drive.google.com/uc?id=1dlajKAkibAWRzNWaUdoFO0OKhVeeBW9w", "pretrained/model.pth", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1_PK1AZCpB7CCBiQsvOm14qr31K20TV9J", "data/pose.json", quiet=False)
elif Person == 'engm':
    gdown.download("https://drive.google.com/uc?id=1P4Fbg5IN_eWxkr7sVQJeK95WVnzV0yGs", "pretrained/model.pth", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1bmkohn1bnxkCJs9Igv5xXIBhyWKoyXMb", "data/pose.json", quiet=False)
elif Person == 'marco':
    gdown.download("https://drive.google.com/uc?id=1XkLbWF3CbvIaLTkjUd7zkdp03um1cyPL", "pretrained/model.pth", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1ETV7yyK3u4MC1ubUQbIvTrRAfJvypcUg", "data/pose.json", quiet=False)
elif Person == 'chris':
    gdown.download("https://drive.google.com/uc?id=1Mx2f1Iu-W9yG8QOn_2ROhhIcrVz4yMeA", "pretrained/model.pth", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1O8uvNuqMo4p0aJi16OMJXLsd1UeQ_7Dw", "data/pose.json", quiet=False)


# audio example
if Audio == 'intro':
    gdown.download("https://drive.google.com/uc?id=1gxfLuYuGFMlYz7BDxJlcfnDISN4sfbKg", "data/intro.wav", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1r2-wJ0VFfahE4bdDzGgvoC2tU24XmxPu", "data/intro_eo.npy", quiet=False)
elif Audio == 'nvp':
    gdown.download("https://drive.google.com/uc?id=1WgtSiB_gLZZ-b8IO_KIVwT_ZRPUSx7yY", "data/nvp.wav", quiet=False)
    gdown.download("https://drive.google.com/uc?id=1UKCW67Idw00_3QqzXasN_dvYXlYC37fe", "data/nvp_eo.npy", quiet=False)


# background image
if Background == 'default':
    gdown.download("https://drive.google.com/uc?id=1RDiRCFXMk3hQ0hzKVculQdFqisayT1MM", "data/bg.jpg", quiet=False)

Downloading...
From: https://drive.google.com/uc?id=1P4Fbg5IN_eWxkr7sVQJeK95WVnzV0yGs
To: /content/RAD-NeRF/pretrained/model.pth
100%|██████████| 17.3M/17.3M [00:00<00:00, 114MB/s] 
Downloading...
From: https://drive.google.com/uc?id=1bmkohn1bnxkCJs9Igv5xXIBhyWKoyXMb
To: /content/RAD-NeRF/data/pose.json
100%|██████████| 2.08M/2.08M [00:00<00:00, 146MB/s]
Downloading...
From: https://drive.google.com/uc?id=1gxfLuYuGFMlYz7BDxJlcfnDISN4sfbKg
To: /content/RAD-NeRF/data/intro.wav
100%|██████████| 752k/752k [00:00<00:00, 119MB/s]
Downloading...
From: https://drive.google.com/uc?id=1r2-wJ0VFfahE4bdDzGgvoC2tU24XmxPu
To: /content/RAD-NeRF/data/intro_eo.npy
100%|██████████| 1.66M/1.66M [00:00<00:00, 156MB/s]
Downloading...
From: https://drive.google.com/uc?id=1RDiRCFXMk3hQ0hzKVculQdFqisayT1MM
To: /content/RAD-NeRF/data/bg.jpg
100%|██████████| 51.3k/51.3k [00:00<00:00, 34.2MB/s]


In [ ]:
#@title Extract audio features
if Audio == 'custom':
    # need to wait to download the ASR model
    %run nerf/asr.py --wav data/{Aud} --save_feats

In [ ]:
#@title Run Inference
%run test.py -O --torso \
    --pose data/pose.json \
    --data_range {Pose_start} {Pose_end} \
    --ckpt pretrained/model.pth \
    --aud data/{Aud[:-4]}_eo.npy \
    --bg_img data/{BG} \
    --workspace trial

Namespace(H=450, O=True, W=450, amb_dim=2, asr=False, asr_model='cpierse/wav2vec2-large-xlsr-53-esperanto', asr_play=False, asr_save_feats=False, asr_wav='', att=2, aud='data/intro_eo.npy', bg_img='data/bg.jpg', bound=1, ckpt='pretrained/model.pth', color_space='srgb', cuda_ray=True, data_range=[0, 100], density_thresh=10, density_thresh_torso=0.01, dt_gamma=0.00390625, emb=False, exp_eye=True, fbg=False, finetune_lips=False, fix_eye=-1, fovy=21.24, fp16=True, fps=50, gui=False, head_ckpt='', ind_dim=4, ind_dim_torso=8, ind_num=10000, l=10, lambda_amb=0.1, m=50, max_ray_batch=4096, max_spp=1, max_steps=16, min_near=0.05, num_rays=65536, num_steps=16, offset=[0, 0, 0], part=False, part2=False, patch_size=1, pose='data/pose.json', r=10, radius=3.35, scale=4, seed=0, smooth_eye=True, smooth_lips=True, smooth_path=True, smooth_path_window=7, test=True, test_train=False, torso=True, torso_shrink=0.8, train_camera=False, update_extra_interval=16, upsample_steps=0, workspace='trial')


[INFO] Trainer: ngp | 2022-11-23_04-39-57 | cuda | fp16 | trial

[INFO] #parameters: 4231701

[INFO] Loading pretrained/model.pth ...

[INFO] loaded model.

...

[INFO] eye_area: 0.25 - 0.25


==> Start Test, save results to trial/results

100% 588/588 [00:57<00:00, 11.38it/s]

==> Finished Test.

100% 588/588 [01:08<00:00,  8.60it/s]


In [ ]:
#@title Display Video

import os
import glob
from IPython.display import HTML
from base64 import b64encode

def get_latest_file(path):
  dir_list = glob.glob(path)
  dir_list.sort(key=lambda x: os.path.getmtime(x))
  return dir_list[-1]
 
Video = get_latest_file(os.path.join('trial', 'results', '*.mp4'))
Video_aud = Video.replace('.mp4', '_aud.mp4')

# concat audio
! ffmpeg -y -i {Video} -i data/{Aud} -c:v copy -c:a aac {Video_aud}

# display
def show_video(video_path, video_width=450):
   
  video_file = open(video_path, "r+b").read()
  video_url = f"data:video/mp4;base64,{b64encode(video_file).decode()}"

  return HTML(f"""<video width={video_width} controls><source src="{video_url}"></video>""")
  
show_video(Video_aud)

ffmpeg version 3.4.11-0ubuntu0.1 Copyright (c) 2000-2022 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-li